In [10]:
import os
import pandas as pd

import sys, copy
from datetime import datetime
sys.path.append('../../Scripts')

from preprocess_daily import DailyPreprocessor

from generate_signals import SignalGenerator

In [11]:
self = DailyPreprocessor()

In [12]:
self.load_data()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


In [13]:
# 2-1-1~7
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()
self.make_matching()

이동류정보 불러오는 중:   0%|          | 0/17280 [00:00<?, ?it/s]

이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:13<00:00, 1296.07it/s]


In [14]:
display(self.match1.head())
display(self.match2.head())
display(self.match3.head())
display(self.match4.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phas_A  phas_B  move_A  move_B
0       175       1       1       8       4
1       175       2       2       7       3
2       175       3       3       6       1
3       175       3       4       6       2
4       175       4       4       5       2

inter_no  phase_no ring_type  move_no
0       175         1         A        8
0       175         1         B        4
1       175         2         A        7
1       175         2         B        3
2       175         3         A        6

inter_no  phase_no ring_type  move_no inc_dir out_dir
0       175         1         A        8       남       북
1       175         1         B        4       북       남
2       175         2         A        7       북       동
3       175         2         B        3       남       서
4       175         3         A        6       동       서

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0       175         1         A        8       남       북       179       004
1       175         1         B        4       북       남       003       176
2       175         2         A        7       북       동       001       095
3       175         2         B        3       남       서       179       270
4       175         3         A        6       동       서       090       270

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A        7       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   

        inc_edge      out_edge node_id inc_edge_id out_edge_id  
0  -571542797_02  571500487_01      i0         NaN         NaN  
1  -571500487_01  571542797_02      i0         NaN         NaN  
2  -571500487_01  571545870_01      i0         NaN         NaN  
3  -571542797_02  571510153_01      i0         NaN         NaN  
4   571545870_02  571510153_01      i0         NaN         NaN

inter_no  move_no inc_dir out_dir       inc_edge      out_edge node_id
0       175        1       동       남   571545870_02  571542797_02      i0
1       175        2       서       동   571510153_02  571545870_01      i0
2       175        3       남       서  -571542797_02  571510153_01      i0
3       175        4       북       남  -571500487_01  571542797_02      i0
4       175        5       서       북   571510153_02  571500487_01      i0

In [ ]:
self.match7 = self.match6.copy()
self.match7 = self.match7[['inter_no', 'move_no', 'inc_dir', 'out_dir', 'inc_edge', 'out_edge', 'node_id']]

# parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
# child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())

# (1) 가능한 (진입방향, 진출방향) 목록 
flows = self.nema.dropna().apply(lambda row: (row['inc_dir'], row['out_dir']), axis=1).tolist()
# (2) 각 교차로별 방향 목록 : pdires (possible directions)
pdires = {}
for node_id in self.parent_ids:
    dires = self.match7[self.match7.node_id == node_id][['inc_dir','out_dir']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    pdires[node_id] = dires
# (3) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id (incoming direction to incoming edge_id)
inc2id = {}
for node_id in self.parent_ids:
    for inc_dir in pdires[node_id]:
        df = self.match7[(self.match7.node_id==node_id) & (self.match7.inc_dir==inc_dir)]
        inc2id[(node_id, inc_dir)] = df.inc_edge.iloc[0]
# (4) 각 (교차로, 진출방향) 별 진출id 목록 : out2id (outgoing direction to outgoing edge_id)
out2id = {}
for node_id in self.parent_ids:
    for out_dir in pdires[node_id]:
        df = self.match7[(self.match7.node_id==node_id) & (self.match7.out_dir==out_dir)]
        out2id[(node_id, out_dir)] = df.out_edge.iloc[0]
# (5) 각 교차로별 가능한 (진입방향, 진출방향) 목록 : pflow (possible flows)
pflow = {}
for node_id in self.parent_ids:
    pflow[node_id] = [flow for flow in flows if set(flow).issubset(pdires[node_id])]
# (6) 가능한 이동류에 대하여 진입id, 진출id 배정 : matching
# node2inter = dict(zip(self.match7['node_id'], self.match7['inter_no']))
dires_right = ['북', '서', '남', '동', '북'] # ex (북, 서), (서, 남) 등은 우회전 flow
self.matching = []
for node_id in self.parent_ids:
    inter_no = self.node2inter[node_id]
    print()
    # 좌회전과 직진(1 ~ 16)
    for (inc_dir, out_dir) in pflow[node_id]:
        move_no = self.nema[(self.nema.inc_dir==inc_dir) & (self.nema.out_dir==out_dir)].move_no.iloc[0]
        inc_edge = inc2id[(node_id, inc_dir)]
        out_edge = out2id[(node_id, out_dir)]
        print(node_id, inter_no, inc_dir, out_dir, move_no, inc_edge, out_edge)
        new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[move_no],
                                'inc_dir':[inc_dir], 'out_dir':[out_dir],
                                'inc_edge':[inc_edge], 'out_edge':[out_edge], 'node_id':[node_id]})
        self.matching.append(new_row)
        display(new_row)
    # 보행신호(17), 전적색(18)
    new_row = pd.DataFrame({'inter_no':[inter_no]*2, 'move_no':[17, 18],
                            'inc_dir':[None]*2, 'out_dir':[None]*2,
                            'inc_edge':[None]*2, 'out_edge':[None]*2, 'node_id':[node_id]*2})
    display(new_row)
    self.matching.append(new_row)
    # 신호우회전(21)
    for d in range(len(dires_right)-1):
        inc_dir = dires_right[d]
        out_dir = dires_right[d+1]
        if {inc_dir, out_dir}.issubset(pdires[node_id]):
            inc_edge = inc2id[(node_id, inc_dir)]
            out_edge = out2id[(node_id, out_dir)]
            new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[21],
                                    'inc_dir':[inc_dir], 'out_dir':[out_dir],
                                    'inc_edge':[inc_edge], 'out_edge':[out_edge], 'node_id':[node_id]})
            display(new_row)
            self.matching.append(new_row)
self.matching.append(self.match7[self.match7.node_id.isin(self.child_ids)])
self.matching = pd.concat(self.matching)
self.matching = self.matching.dropna().sort_values(by=['inter_no', 'node_id', 'move_no']).reset_index(drop=True)
self.matching['move_no'] = self.matching['move_no'].astype(int)

In [47]:
display(pdires)

{'i0': {'남', '동', '북', '서'},
 'i1': {'남', '북', '서'},
 'i2': {'남', '동', '북', '서'},
 'i3': {'남', '동', '북', '서'},
 'i6': {'남', '동', '북', '서'},
 'i7': {'남', '북'},
 'i8': {'남', '동', '북', '서'},
 'i9': {'동', '서'}}

In [62]:
inc_dir2angles = dict()
out_dir2angles = dict()
for inter_no in self.match4.inter_no.unique():
    df = self.match4[self.match4.inter_no==inter_no].dropna()
    inc_dir2angle = dict(zip(df['inc_dir'], df['inc_angle']))
    out_dir2angle = dict(zip(df['out_dir'], df['out_angle']))
    inc_dir2angles[inter_no] = inc_dir2angle
    out_dir2angles[inter_no] = out_dir2angle
display(inc_dir2angles)
display(out_dir2angles)

{175: {'남': '179', '북': '001', '동': '090', '서': '270'},
 176: {'남': '180', '북': '359', '서': '270'},
 177: {'남': '179', '북': '000', '서': '268', '동': '090'},
 178: {'남': '180', '북': '000', '서': '270', '동': '090'},
 201: {'남': '180', '서': '270', '동': '090', '북': '000'},
 202: {'동': '090', '서': '270'},
 206: {'남': '180', '북': '000'},
 210: {'동': '090', '서': '270', '북': '000', '남': '180'}}

{175: {'북': '000', '남': '180', '동': '090', '서': '270'},
 176: {'북': '356', '남': '180', '서': '270'},
 177: {'북': '000', '남': '180', '동': '090', '서': '270'},
 178: {'북': '000', '남': '180', '동': '090', '서': '270'},
 201: {'북': '000', '서': '270', '동': '090', '남': '180'},
 202: {'서': '270', '동': '090'},
 206: {'북': '000', '남': '180'},
 210: {'서': '270', '북': '000', '동': '090', '남': '180'}}

In [85]:
display(inc_dire, out_dire)

'남'

'북'

In [108]:
angles = []
for inter_no in self.inter_nos:
    node_id = self.inter2node[inter_no]
    flows = pflow[node_id]
    inc_dir2angle = inc_dir2angles[inter_no]
    out_dir2angle = out_dir2angles[inter_no]
    for (inc_dire, out_dire) in flows:
        inc_angle = inc_dir2angle[inc_dire]
        out_angle = out_dir2angle[out_dire]
        angle_code = inc_angle + out_angle
        nema_row = self.nema[(self.nema.inc_dir==inc_dire)&(self.nema.out_dir==out_dire)]
        move_no = nema_row.iloc[0].move_no
        angle = pd.DataFrame({'inter_no':[inter_no],'move_no':[move_no], 'angle_code':[angle_code]})
        angles.append(angle)
angles = pd.concat(angles)
angles

inter_no  move_no angle_code
0       175        1     090180
0       175        2     270090
0       175        3     179270
0       175        4     001180
0       175        5     270000
0       175        6     090270
0       175        7     001090
0       175        8     179000
0       176        3     180270
0       176        4     359180
0       176        5     270356
0       176        8     180356
0       177        1     090180
0       177        2     268090
0       177        3     179270
0       177        4     000180
0       177        5     268000
0       177        6     090270
0       177        7     000090
0       177        8     179000
0       178        1     090180
0       178        2     270090
0       178        3     180270
0       178        4     000180
0       178        5     270000
0       178        6     090270
0       178        7     000090
0       178        8     180000
0       201        1     090180
0       201        2     270090
0       201        3     180270
0       201        4     000180
0       201        5     270000
0       201        6     090270
0       201        7     000090
0       201        8     180000
0       202        2     270090
0       202        6     090270
0       206        4     000180
0       206        8     180000
0       210        1     090180
0       210        2     270090
0       210        3     180270
0       210        4     000180
0       210        5     270000
0       210        6     090270
0       210        7     000090
0       210        8     180000

In [63]:
pflow

{'i0': [('동', '남'),
  ('서', '동'),
  ('남', '서'),
  ('북', '남'),
  ('서', '북'),
  ('동', '서'),
  ('북', '동'),
  ('남', '북')],
 'i1': [('남', '서'), ('북', '남'), ('서', '북'), ('남', '북')],
 'i2': [('동', '남'),
  ('서', '동'),
  ('남', '서'),
  ('북', '남'),
  ('서', '북'),
  ('동', '서'),
  ('북', '동'),
  ('남', '북')],
 'i3': [('동', '남'),
  ('서', '동'),
  ('남', '서'),
  ('북', '남'),
  ('서', '북'),
  ('동', '서'),
  ('북', '동'),
  ('남', '북')],
 'i6': [('동', '남'),
  ('서', '동'),
  ('남', '서'),
  ('북', '남'),
  ('서', '북'),
  ('동', '서'),
  ('북', '동'),
  ('남', '북')],
 'i7': [('북', '남'), ('남', '북')],
 'i8': [('동', '남'),
  ('서', '동'),
  ('남', '서'),
  ('북', '남'),
  ('서', '북'),
  ('동', '서'),
  ('북', '동'),
  ('남', '북')],
 'i9': [('서', '동'), ('동', '서')]}

In [23]:
display(self.match6)
display(self.matching)

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B        2       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge      out_edge node_id inc_edge_id out_edge_id  
0   -571542797_02  571500487_01      i0         NaN         NaN  
1   -571500487_01  571542797_02      i0         NaN         NaN  
2   -571500487_01  571545870_01      i0         NaN         NaN  
3   -571542797_02  571510153_01      i0         NaN         NaN  
4    571545870_02  571510153_01      i0         NaN         NaN  
..            ...           ...     ...         ...         ...  
3             NaN           NaN     u60         NaN         NaN  
4             NaN           NaN     u60         NaN         NaN  
5             NaN           NaN     u60         NaN         NaN  
6             NaN           NaN     u60         NaN         NaN  
7             NaN           NaN     u60         NaN         NaN  

[116 rows x 13 columns]

inter_no  move_no inc_dir out_dir          inc_edge       out_edge node_id
0        175        1       동       남      571545870_02   571542797_02      i0
1        175        2       서       동      571510153_02   571545870_01      i0
2        175        3       남       서     -571542797_02   571510153_01      i0
3        175        4       북       남     -571500487_01   571542797_02      i0
4        175        5       서       북      571510153_02   571500487_01      i0
..       ...      ...     ...     ...               ...            ...     ...
71       210       21       북       서  571511538_02.121   571500535_01      i6
72       210       21       서       남   571500535_02.18   571500585_01      i6
73       210       21       남       동      571500585_02   571542115_01      i6
74       210       21       동       북     -571542115_01   571511538_01      i6
75       210        5       서       북      571500535_02  -571500535_02     u60

[76 rows x 7 columns]

In [ ]:
sg = SignalGenerator()
sg.main()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.
5. 신호를 생성합니다.
6. 이슈사항을 저장합니다.
(1) 0:00:00.141398
(1-1) 0:00:00.025139
(1-2) 0:00:00.061132
(1-3) 0:00:00
(1-4) 0:00:00
(1-5) 0:00:00.055127
(2) 0:00:00.294164
(2-1) 0:00:00.064693
(2-2) 0:00:00.196721
(2-3) 0:00:00.032750
(3) 0:00:00.461845
(3-1) 0:00:00.437385
(3-2) 0:00:00.024460
(4) 0:00:00.188478
(4-1) 0:00:00.006985
(4-2) 0:00:00.015015
(4-2) 0:00:00.166478
(5) 0:00:00.787933
(5-1) 0:00:00.016678
(5-2) 0:00:00.770144
(5-3) 0:00:00.001111
(6) 0:00:00
total time : 0:00:01.873818


In [ ]:
sg.movedur

inter_no  start_unix  phas_A  phas_B  move_A  move_B  duration
0         201  1704418940       1       1       8       3        33
1         201  1704418940       2       2       5       2        36
2         201  1704418940       3       3       6       2        25
3         201  1704418940       4       4       6       1        58
4         201  1704418940       5       5       7       4        18
..        ...         ...     ...     ...     ...     ...       ...
253       177  1704419870       4       4       5       1        40
254       177  1704420050       1       1       8       4        43
255       177  1704420050       2       2       7       3        27
256       177  1704420050       3       3      17      18        70
257       177  1704420050       4       4       5       1        40

[258 rows x 7 columns]

In [13]:
print(len(self.match5))
print(len(self.match6))

60
116


In [5]:
self.directions

['북', '북동', '동', '남동', '남', '남서', '서', '북서']

In [7]:
import numpy as np

# dictionary that maps dire(북) to dir(np.array([0,1]))
self.dire2dir = dict()
theta = np.pi/2
for dire in self.directions:
    self.dire2dir[dire] = np.array([np.cos(theta), np.sin(theta)])
    theta -= np.pi/4
self.dire2dir

{'북': array([6.123234e-17, 1.000000e+00]),
 '북동': array([0.70710678, 0.70710678]),
 '동': array([1., 0.]),
 '남동': array([ 0.70710678, -0.70710678]),
 '남': array([ 6.123234e-17, -1.000000e+00]),
 '남서': array([-0.70710678, -0.70710678]),
 '서': array([-1.0000000e+00, -1.2246468e-16]),
 '북서': array([-0.70710678,  0.70710678])}

In [22]:
node_id = 'i5'
node = self.net.getNode(node_id)
inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
inc_edge = inc_edges[0]
loc_inc_edge = inc_edge.getShape()[-1]
node.getShape()

[(10315.19, 11460.86),
 (10314.85, 11439.86),
 (10314.54, 11439.86),
 (10314.9, 11460.86)]

In [5]:
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [15]:
for node_id in self.node_ids:
    print(node_id)
    node = self.net.getNode(node_id)
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    inc_edge_ids = [edge.getID() for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edge ids
    out_edge_ids = [edge.getID() for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edge ids
    # print(node)
    for inc_edge_id in inc_edge_ids:
        print(inc_edge_id)

c30
571542116_01
571542116_02.96
i0
-571500487_01
-571542797_02
571510153_02
571545870_02
i1
-571542810_01
571542797_02.99
571543469_02
i2
-571542809_01
571542107_02
571542811_02
i3
-571500475_01
571540303_02.21
571540304_02
571556450_02
i6
-571542115_01
571500535_02.18
571500585_02
571511538_02.121
i7
-571511538_02
571542071_02
571542073_01
i8
-571500569_01
571500583_01
571500617_02
571500618_02
i9
571510152_01
571510152_02
u00
571500487_01
571500487_02
u20
571542810_01.51
571542811_01
u30
571556450_01
571556452_01
u31
571500475_01
571500475_02
u32
571540303_01
571540303_02
u60
571500535_01
571500535_02


In [10]:
self.matching

inter_no  move_no inc_dir out_dir          inc_edge       out_edge node_id
0        175        1       동       남      571545870_02   571542797_02      i0
1        175        2       서       동      571510153_02   571545870_01      i0
2        175        3       남       서     -571542797_02   571510153_01      i0
3        175        4       북       남     -571500487_01   571542797_02      i0
4        175        5       서       북      571510153_02   571500487_01      i0
..       ...      ...     ...     ...               ...            ...     ...
71       210       21       북       서  571511538_02.121   571500535_01      i6
72       210       21       서       남   571500535_02.18   571500585_01      i6
73       210       21       남       동      571500585_02   571542115_01      i6
74       210       21       동       북     -571542115_01   571511538_01      i6
75       210        5       서       북      571500535_02  -571500535_02     u60

[76 rows x 7 columns]

In [5]:
self.directions

['북', '북동', '동', '남동', '남', '남서', '서', '북서']

In [10]:
list(self.node_id2inc_edge2dir['i0'])[1]

'-571542797_02'

In [25]:
self.node_id2inc_edge2dir['i0']

{'-571500487_01': array([-0.00936558, -0.99995614]),
 '-571542797_02': array([0.00318883, 0.99999492]),
 '571510153_02': array([0.99927006, 0.03820147]),
 '571545870_02': array([-0.99951221,  0.03123044])}

In [45]:
self.dire2dir

{'북': array([6.123234e-17, 1.000000e+00]),
 '북동': array([0.70710678, 0.70710678]),
 '동': array([1., 0.]),
 '남동': array([ 0.70710678, -0.70710678]),
 '남': array([ 6.123234e-17, -1.000000e+00]),
 '남서': array([-0.70710678, -0.70710678]),
 '서': array([-1.0000000e+00, -1.2246468e-16]),
 '북서': array([-0.70710678,  0.70710678])}

In [56]:
self.node_id2inc_edge2dir['i0']

{'-571500487_01': array([-0.00936558, -0.99995614]),
 '-571542797_02': array([0.00318883, 0.99999492]),
 '571510153_02': array([0.99927006, 0.03820147]),
 '571545870_02': array([-0.99951221,  0.03123044])}

In [53]:
import numpy as np

# dictionary that maps dire(북) to dir(np.array([0,1]))
self.dire2dir = dict()
theta = np.pi/2
for dire in self.directions:
    self.dire2dir[dire] = np.array([np.cos(theta), np.sin(theta)])
    theta -= np.pi/4

# dictionary that maps node_id and inc_edge_id to direction(북)
self.node_id2inc_edge2dire = dict()
for node_id in self.parent_ids:
    inc_edge2dire = dict()
    node = self.net.getNode(node_id)
    inc_edges = [inc_edge.getID() for inc_edge in node.getIncoming()]
    out_edges = [out_edge.getID() for out_edge in node.getOutgoing()]

    for inc_edge in inc_edges:
        inc_dir_true = self.node_id2inc_edge2dir[node_id][inc_edge]
        inc_dirs = [self.dire2dir[inc_dire] for inc_dire in self.directions]
        inc_index = np.array([np.dot(inc_dir, inc_dir_true) for inc_dir in inc_dirs]).argmax()
        print(inc_index)
        print(self.directions[inc_index])
        for inc_dir in inc_dirs:
            print(inc_dir)
            print(inc_dir_true)
            print(np.dot(inc_dir, inc_dir_true))
            print()
        inc_edge2dire[inc_edge] = self.directions[inc_index]
    self.node_id2inc_edge2dire[node_id] = inc_edge2dire
self.node_id2inc_edge2dire['i0']

4
남
[6.123234e-17 1.000000e+00]
[-0.00936558 -0.99995614]
-0.999956141961442

[0.70710678 0.70710678]
[-0.00936558 -0.99995614]
-0.7136982364459966

[1. 0.]
[-0.00936558 -0.99995614]
-0.00936558346224636

[ 0.70710678 -0.70710678]
[-0.00936558 -0.99995614]
0.7004533012941507

[ 6.123234e-17 -1.000000e+00]
[-0.00936558 -0.99995614]
0.999956141961442

[-0.70710678 -0.70710678]
[-0.00936558 -0.99995614]
0.7136982364459966

[-1.0000000e+00 -1.2246468e-16]
[-0.00936558 -0.99995614]
0.009365583462246483

[-0.70710678  0.70710678]
[-0.00936558 -0.99995614]
-0.7004533012941506

0
북
[6.123234e-17 1.000000e+00]
[0.00318883 0.99999492]
0.9999949156539597

[0.70710678 0.70710678]
[0.00318883 0.99999492]
0.7093580325944496

[1. 0.]
[0.00318883 0.99999492]
0.0031888346194069504

[ 0.70710678 -0.70710678]
[0.00318883 0.99999492]
-0.7048483394275195

[ 6.123234e-17 -1.000000e+00]
[0.00318883 0.99999492]
-0.9999949156539597

[-0.70710678 -0.70710678]
[0.00318883 0.99999492]
-0.7093580325944496

[-1.000

{'-571500487_01': '남',
 '-571542797_02': '북',
 '571510153_02': '동',
 '571545870_02': '서'}

In [8]:
match6 = self.match6.copy()
matching = self.matching.copy()
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [112]:
self.match6 = match6
self.matching=matching

In [100]:
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [101]:
self.match6

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B        2       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge      out_edge node_id  
0   -571542797_02  571500487_01      i0  
1   -571500487_01  571542797_02      i0  
2   -571500487_01  571545870_01      i0  
3   -571542797_02  571510153_01      i0  
4    571545870_02  571510153_01      i0  
..            ...           ...     ...  
3             NaN           NaN     u60  
4             NaN           NaN     u60  
5             NaN           NaN     u60  
6             NaN           NaN     u60  
7             NaN           NaN     u60  

[116 rows x 11 columns]

In [77]:
# node = self.net.getNode(node_id)
# conns = list(node.getConnections())
# print(node_id)
# for con in node.getConnections():
#     print(con)
# print()
# for con in conns:
#     print(con)

In [71]:
all_conns = list(node.getConnections())
allocated_conns = []
# display(matching)
row = self.matching.iloc[0]
node_id = row.node_id
move_no = row.move_no
inc_edge = row.inc_edge
out_edge = row.out_edge
state = copy.deepcopy(self.node2init)[node_id]

node = self.net.getNode(node_id)

print(node_id)
print(state)
print(inc_edge)
print(out_edge)
inc_edge = self.net.getEdge(inc_edge)
out_edge = self.net.getEdge(out_edge)
# incoming edge, outgoing edge가 지정된 이동류에 대하여
for conn in inc_edge.getConnections(out_edge):
    allocated_conns.append(conns)
    print(conn)
    index = conn.getTLLinkIndex()
    if index >= 0:
        # 신호를 G로 지정
        state[index] = 'G'
print(state)
for conn in allocated_conns:
    print(conn)

i0
['g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r']
571545870_02
571542797_02
<connection from="571545870_02" to="571542797_02" fromLane="0" toLane="1" tl="i0" linkIndex="7" direction="l">
['g', 'r', 'r', 'r', 'g', 'r', 'r', 'G', 'g', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r']
[<sumolib.net.connection.Connection object at 0x0000022B6D65A400>, <sumolib.net.connection.Connection object at 0x0000022B6D65A460>, <sumolib.net.connection.Connection object at 0x0000022B6D65A490>, <sumolib.net.connection.Connection object at 0x0000022B6D65A4C0>, <sumolib.net.connection.Connection object at 0x0000022B6D65AB80>, <sumolib.net.connection.Connection object at 0x0000022B6D65ABB0>, <sumolib.net.connection.Connection object at 0x0000022B6D65ABE0>, <sumolib.net.connection.Connection object at 0x0000022B6D65AC10>, <sumolib.net.connection.Connection object at 0x0000022B6D65AC40>, <sumolib.net.connection.Connection object at 0x0000022B6D65AC70>, <sumolib.net.connection.Con

In [84]:
node_id = self.node_ids[0]
node = self.net.getNode(node_id)
node

<junction id="c30"/>

In [121]:
node2conns = dict()
node2allocated_conns = dict()
for node_id in self.node_ids:
    node = self.net.getNode(node_id)
    node2conns[node_id] = list(node.getConnections())
    node2allocated_conns[node_id] = []

In [120]:
self.match6 = match6
self.matching=matching

In [122]:
self.matching['init_state'] = self.matching['node_id'].map(self.node2init)
self.matching['state'] = self.matching['init_state'].map(lambda x:''.join(x))
    
node2allocated_conns = dict()
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            node2allocated_conns[node_id].append(conn)
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'state']]


KeyError: 'i0'

In [ ]:
node2allocated_conns

In [57]:
self.assign_signals()

2-3. 직진 및 좌회전(G)을 배정했습니다.


In [62]:
match6

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0        175         1         A        8       남       북       179       004   
1        175         1         B        4       북       남       003       176   
2        175         2         A        7       북       동       001       095   
3        175         2         B        3       남       서       179       270   
4        175         3         A        6       동       서       090       270   
..       ...       ...       ...      ...     ...     ...       ...       ...   
3        210         2         B        2       서       동       270       090   
4        210         3         A        7       북       동       359       090   
5        210         3         B        4       북       남       000       180   
6        210         4         A        8       남       북       180       000   
7        210         4         B        3       남       서       180       270   

         inc_edge      out_edge node_id  
0   -571542797_02  571500487_01      i0  
1   -571500487_01  571542797_02      i0  
2   -571500487_01  571545870_01      i0  
3   -571542797_02  571510153_01      i0  
4    571545870_02  571510153_01      i0  
..            ...           ...     ...  
3             NaN           NaN     u60  
4             NaN           NaN     u60  
5             NaN           NaN     u60  
6             NaN           NaN     u60  
7             NaN           NaN     u60  

[116 rows x 11 columns]

In [58]:
self.match6

inter_no node_id  phase_no ring_type  move_no              state
0         175      i0         1         A        8  grrrgrrrgGGGGrgrr
1         175      i0         1         B        4  gGGrgrrrgrrrrrgrr
2         175      i0         2         A        7  grrGgrrrgrrrrrgrr
3         175      i0         2         B        3  grrrgrrrgrrrrGgrr
4         175      i0         3         A        6  grrrgGGrgrrrrrgrr
..        ...     ...       ...       ...      ...                ...
111       210     u60         2         B        2          ggggggggr
112       210     u60         3         A        7          ggggggggr
113       210     u60         3         B        4          ggggggggr
114       210     u60         4         A        8          ggggggggr
115       210     u60         4         B        3          ggggggggr

[116 rows x 6 columns]

In [25]:
self.match6

inter_no node_id  phase_no ring_type  move_no              state
0         175      i0         1         A        8  grrrgrrrgGGGGrgrr
1         175      i0         1         B        4  gGGrgrrrgrrrrrgrr
2         175      i0         2         A        7  grrGgrrrgrrrrrgrr
3         175      i0         2         B        3  grrrgrrrgrrrrGgrr
4         175      i0         3         A        6  grrrgGGrgrrrrrgrr
..        ...     ...       ...       ...      ...                ...
111       210     u60         2         B        2          ggggggggr
112       210     u60         3         A        7          ggggggggr
113       210     u60         3         B        4          ggggggggr
114       210     u60         4         A        8          ggggggggr
115       210     u60         4         B        3          ggggggggr

[116 rows x 6 columns]